In [1]:
from gensim.models.keyedvectors import KeyedVectors
from keras.preprocessing.text import Tokenizer
#model = FastText.load_word2vec_format('crawl-300d-2M.vec')
import pandas as pd
import numpy as np

import enchant
import splitter
from sklearn.model_selection import StratifiedKFold
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import GridSearchCV


/home/dcek/anaconda2/envs/py27/lib/python2.7/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


In [2]:
word_vectors = KeyedVectors.load_word2vec_format('git/Kaggle/data/crawl-300d-2M.vec', binary=False)


In [3]:
print(word_vectors.most_similar('teacher'))


[(u'teachers', 0.775285542011261), (u'Teacher', 0.7537139654159546), (u'teacher.', 0.7064430713653564), (u'educator', 0.701554536819458), (u'student', 0.6865893602371216), (u'teaher', 0.6860877275466919), (u'teacher-', 0.6852282881736755), (u'teacher.So', 0.664068877696991), (u'teacer', 0.6594300270080566), (u'teacher.I', 0.6572564244270325)]


In [50]:
words = ["gayyyyyyyyyyy","fuk1ng"]
#pleeeeeeeeeeeeeaaaaaaaaaaaaaaaaaaaaaassssssssssssssssseeeeeeeeeeeee
split_t = splitter.split('helloboy')
if split_t is "":
    print("Noone")
else:
    for s in split_t:
        print("Not in vocab : {}".format(s))
d = enchant.Dict("en_US")
try:
    print(d.suggest("")[0])
except KeyError:
    print("")  
wo = ''.join(e for e in words[1] if e.isalnum())
wo = ''.join([i for i in words[1] if not i.isdigit()])
print(wo)
for w in words:
    try:
        w = ''.join(e for e in w if e.isalnum())
        w = ''.join([i for i in w if not i.isdigit()])
        print(word_vectors.most_similar(w)[0][0])
    except KeyError:
        print ("not in vocabulary")

Not in vocab : hello
Not in vocab : boy


ValueError: can't suggest spellings for empty string

In [17]:
#extra = pd.read_csv('stage_one_ensemble_features/extra_feature.csv')
#xgb = pd.read_csv('stage_one_ensemble_features/meta_xgbcv.csv')
#nbsvm = pd.read_csv('stage_one_ensemble_features/meta_nbsvmaugment.csv')
#gru = pd.read_csv('stage_one_ensemble_features/meta_gruCV.csv')

extra = pd.read_csv('stage_one_ensemble_features/test/test_extra_feature.csv')
xgb = pd.read_csv('stage_one_ensemble_features/test/xgbcv.csv')
nbsvm = pd.read_csv('stage_one_ensemble_features/test/nbsvm_CV_final_submission.csv')
gru = pd.read_csv('stage_one_ensemble_features/test/final_GRU_CV.csv')





In [18]:
xgb = xgb[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']]
nbsvm = nbsvm[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']]
gru = gru[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']]

xgb.columns = ['toxic-a', 'severe_toxic-a', 'obscene-a', 'threat-a', 'insult-a', 'identity_hate-a']
nbsvm.columns = ['toxic-b', 'severe_toxic-b', 'obscene-b', 'threat-b', 'insult-b', 'identity_hate-b']
gru.columns = ['toxic-c', 'severe_toxic-c', 'obscene-c', 'threat-c', 'insult-c', 'identity_hate-c']

final_label = ['capitals','num_unique_words', 'num_exclamation_marks', 'num_punctuation', 'toxic-a', 'severe_toxic-a', 'obscene-a', 'threat-a', 'insult-a', 'identity_hate-a','toxic-b', 'severe_toxic-b', 'obscene-b', 'threat-b', 'insult-b', 'identity_hate-b','toxic-c', 'severe_toxic-c', 'obscene-c', 'threat-c', 'insult-c', 'identity_hate-c']

In [19]:
display(gru.head(n=20))


toxic-c  severe_toxic-c  obscene-c      threat-c      insult-c  \
0   0.999513    5.849002e-01   0.998180  3.962921e-02  9.923904e-01   
1   0.000011    8.483525e-08   0.000003  3.578422e-08  2.472466e-06   
2   0.000048    1.422525e-06   0.000018  5.416999e-07  1.094320e-05   
3   0.000011    1.834970e-07   0.000002  1.400543e-07  1.410444e-06   
4   0.000701    6.848788e-06   0.000091  2.167931e-06  1.946919e-05   
5   0.000114    1.147158e-06   0.000045  7.456309e-07  1.287611e-05   
6   0.000025    3.722964e-07   0.000008  3.971901e-07  6.427652e-06   
7   0.303759    1.878642e-04   0.004547  2.195808e-06  5.638059e-03   
8   0.013517    2.809659e-06   0.000214  1.816253e-07  6.337736e-04   
9   0.000010    1.142003e-07   0.000002  3.789257e-07  1.224494e-06   
10  0.508850    3.884607e-04   0.277840  1.190992e-05  4.030364e-03   
11  0.000034    2.209418e-07   0.000017  2.818283e-08  4.439093e-06   
12  0.000015    5.602973e-08   0.000005  2.993845e-08  8.351560e-07   
13  0.000018    4.370605e-08   0.000003  1.613685e-08  1.563223e-06   
14  0.000007    5.550302e-08   0.000002  2.470779e-08  5.977466e-07   
15  0.000196    7.188201e-07   0.000028  1.225561e-07  1.659652e-05   
16  0.000136    1.450659e-06   0.000053  3.014552e-07  1.030126e-05   
17  0.000033    1.436291e-07   0.000010  2.682841e-08  2.114226e-06   
18  0.000025    1.115218e-07   0.000007  4.167451e-08  1.655056e-06   
19  0.000940    1.006817e-05   0.000181  8.606301e-06  1.240416e-04   

    identity_hate-c  
0      3.324885e-01  
1      9.323965e-07  
2      6.734834e-06  
3      4.894738e-07  
4      5.549907e-06  
5      4.240550e-06  
6      9.556097e-07  
7      1.276561e-04  
8      6.001245e-06  
9      3.552336e-07  
10     1.459329e-05  
11     6.213128e-06  
12     2.931875e-07  
13     3.651157e-07  
14     3.028973e-07  
15     1.505569e-06  
16     7.587026e-06  
17     5.504835e-07  
18     3.464335e-07  
19     9.897426e-06

In [9]:
submission = pd.concat([extra, xgb], axis=1)


In [10]:
submission = pd.concat([submission, nbsvm], axis =1)
submission = pd.concat([submission, gru], axis =1)

In [15]:
display(submission.head(n=5))
submission.to_csv('meta_ensemble_train.csv', index=False)

id  capitals  num_unique_words  num_exclamation_marks  \
0  0000997932d777bf  2.890372          3.737670                      0   
1  000103f0d9cfb60f  2.197225          2.890372                      1   
2  000113f07ec002fd  1.609438          3.688879                      0   
3  0001b41b1c6bb37e  2.484907          4.418841                      0   
4  0001d958c54c6e35  1.098612          2.639057                      0   

   num_punctuation   toxic-a  severe_toxic-a  obscene-a  threat-a  insult-a  \
0         1.945910  0.020052        0.000172   0.004895  0.000009  0.004707   
1         1.791759  0.120857        0.003638   0.057968  0.000012  0.037449   
2         1.609438  0.013945        0.000713   0.002814  0.000004  0.003211   
3         1.945910  0.000969        0.000030   0.000708  0.000010  0.000387   
4         1.386294  0.065857        0.000799   0.037083  0.000079  0.029953   

        ...         obscene-b  threat-b  insult-b  identity_hate-b   toxic-c  \
0       ...          0.000439  0.000002  0.000171         0.000027  0.000022   
1       ...          0.000401  0.000034  0.000035         0.000243  0.000093   
2       ...          0.002197  0.000116  0.000982         0.000057  0.000027   
3       ...          0.000172  0.000044  0.000013         0.000113  0.000003   
4       ...          0.004972  0.000167  0.011593         0.001136  0.055592   

   severe_toxic-c     obscene-c      threat-c      insult-c  identity_hate-c  
0    3.138842e-08  2.994806e-06  4.430928e-08  5.518635e-07         0.000002  
1    3.662976e-07  2.097395e-05  3.905927e-06  1.274817e-04         0.000019  
2    9.877562e-08  1.275927e-05  3.604457e-07  2.372584e-06         0.000002  
3    6.143312e-09  5.066889e-07  3.393286e-07  3.782168e-07         0.000002  
4    1.395989e-04  2.420142e-03  9.266990e-05  1.299712e-02         0.002872  

[5 rows x 23 columns]

In [14]:
submission

(638284, 23)

In [2]:
train = pd.read_csv('stage_one_ensemble_features/combined_meta.csv')
display(train.head(n=20))

id  capitals  num_unique_words  num_exclamation_marks  \
0   0000997932d777bf  2.890372          3.737670                      0   
1   000103f0d9cfb60f  2.197225          2.890372                      1   
2   000113f07ec002fd  1.609438          3.688879                      0   
3   0001b41b1c6bb37e  2.484907          4.418841                      0   
4   0001d958c54c6e35  1.098612          2.639057                      0   
5   00025465d4725e87  0.693147          2.564949                      0   
6   0002bcb3da6cb337  3.637586          2.197225                      0   
7   00031b1e95af7921  1.609438          3.044522                      0   
8   00037261f536c51d  2.079442          4.262680                      0   
9   00040093b2687caa  1.098612          2.564949                      0   
10  0005300084f90edc  3.988984          5.402677                      0   
11  00054a5e18b50dd4  0.000000          2.484907                      0   
12  0005c987bdfc9d4b  3.784190          3.931826                      0   
13  0006f16e4e9f292e  1.945910          4.691348                      0   
14  00070ef96486d6f9  2.197225          3.465736                      0   
15  00078f8ce7eb276d  3.367296          4.543295                      0   
16  0007e25b2121310b  1.386294          2.397895                      2   
17  000897889268bc93  2.639057          1.791759                      0   
18  0009801bd85e5806  1.791759          2.995732                      0   
19  0009eaea3325de8c  1.791759          4.143135                      0   

    num_punctuation   toxic-a  severe_toxic-a  obscene-a  threat-a  insult-a  \
0          1.945910  0.020052        0.000172   0.004895  0.000009  0.004707   
1          1.791759  0.120857        0.003638   0.057968  0.000012  0.037449   
2          1.609438  0.013945        0.000713   0.002814  0.000004  0.003211   
3          1.945910  0.000969        0.000030   0.000708  0.000010  0.000387   
4          1.386294  0.065857        0.000799   0.037083  0.000079  0.029953   
5          1.098612  0.008962        0.000155   0.005418  0.000125  0.006372   
6          0.000000  0.948445        0.546873   0.964787  0.002511  0.870642   
7          1.386294  0.077494        0.000849   0.035757  0.004910  0.022695   
8          2.302585  0.009515        0.000058   0.002625  0.000006  0.002876   
9          0.000000  0.044735        0.001380   0.014605  0.000127  0.023963   
10         4.043051  0.003349        0.000048   0.001828  0.000005  0.000275   
11         0.000000  0.053676        0.002421   0.018360  0.001199  0.009410   
12         2.833213  0.048584        0.000060   0.012649  0.000019  0.002401   
13         2.708050  0.092242        0.000094   0.005338  0.000096  0.024431   
14         2.079442  0.074170        0.001610   0.052821  0.000040  0.017798   
15         2.772589  0.023108        0.003158   0.008163  0.000053  0.006666   
16         1.098612  0.124986        0.003207   0.035925  0.000557  0.032427   
17         0.693147  0.022920        0.000626   0.005541  0.000098  0.005105   
18         0.000000  0.030039        0.001578   0.003491  0.000011  0.014697   
19         1.386294  0.026125        0.000289   0.006253  0.000100  0.010717   

         ...            obscene-b      threat-b  insult-b  identity_hate-b  \
0        ...         4.386071e-04  1.589602e-06  0.000171         0.000027   
1        ...         4.014467e-04  3.413729e-05  0.000035         0.000243   
2        ...         2.197055e-03  1.161840e-04  0.000982         0.000057   
3        ...         1.717578e-04  4.425572e-05  0.000013         0.000113   
4        ...         4.972179e-03  1.665751e-04  0.011593         0.001136   
5        ...         2.247388e-07  3.394539e-07  0.000006         0.000009   
6        ...         8.258977e-01  2.701001e-04  0.296263         0.002003   
7        ...         3.699794e-04  5.190443e-04  0.001582         0.000912   
8        ...         5.198229e-05  1.697967e-06  0.000014  

In [ ]:
train

In [27]:
train_data = pd.read_csv('git/Kaggle/train.csv')


In [3]:
def fit_and_save_tokenizer(texts):
    """Fits tokenizer on texts and pickles the tokenizer state."""
    tokenizer = Tokenizer(num_words=10000)
    tokenizer.fit_on_texts(texts)
    return tokenizer
def load_embeddings(tokenizer, word_vectors):
    
    embeddings_path = 'git/Kaggle/data/glove.6B/glove.840B.300d.txt'
    embeddings_index = {}
    with open(embeddings_path) as f:
        for line in f:
            values = line.split()
            word = values[0]
            coefs = np.asarray(values[1:], dtype='float32')
            embeddings_index[word] = coefs

    embedding_matrix = np.zeros((len(tokenizer.word_index) + 1,
                                      300))
    num_words_in_embedding = 0
    num_words_replaced = 0
    num_words_fail_replaced = 0
    for word, i in tokenizer.word_index.items():
        embedding_vector = embeddings_index.get(word)
        if embedding_vector is not None:
            num_words_in_embedding += 1
            # words not found in embedding index will be all-zeros.
            embedding_matrix[i] = embedding_vector
        else:
            word = ''.join(e for e in word if e.isalnum())
            word = ''.join([f for f in word if not f.isdigit()])
            try:               
                replace_word = word_vectors.most_similar(word)[0][0]
                embedding_vector_second = embeddings_index.get(replace_word)
                if embedding_vector_second is not None:
                    num_words_in_embedding += 1
                    embedding_matrix[i] = embedding_vector_second
                    num_words_replaced += 1
                else:
                    split_trial = splitter.split(replace_word)
                    if split_trial is not "":
                        for wrd in split_trial:
                            embedding_vector_third = embeddings_index.get(wrd)
                            if embedding_vector_third is not None:
                                num_words_in_embedding += 1
                                embedding_matrix[i] = embedding_vector_third
                                num_words_replaced += 1                              
                            else:
                                num_words_fail_replaced += 1
                                print(" not in vocabulary")
                    else:
                        d = enchant.Dict("en_US")
                        wrd = d.suggest(replace_word)
                        if not wrd:
                            num_words_fail_replaced += 1
                            print("{} not in vocabulary List is empty".format(wrd))
                        else:
                            wrd = wrd[0]
                            wrd = ''.join(e for e in wrd if e.isalnum())
                            wrd = ''.join([f for f in wrd if not f.isdigit()])
                            embedding_vector_fourth = embeddings_index.get(wrd)
                            if embedding_vector_fourth is not None:
                                num_words_in_embedding += 1
                                embedding_matrix[i] = embedding_vector_fourth
                                num_words_replaced += 1                              
                            else:
                                num_words_fail_replaced += 1
                                print(" not in vocabulary")

            except KeyError:
                d = enchant.Dict("en_US")
                if word == "":
                    num_words_fail_replaced += 1
                    print("{} not in vocabulary".format(word))
                else:
                    wrd = d.suggest(word)
                    if not wrd:
                        num_words_fail_replaced += 1
                        print("{} not in vocabulary List is empty".format(wrd))
                    else:
                        wrd = wrd[0]
                        wrd = ''.join(e for e in wrd if e.isalnum())
                        wrd = ''.join([f for f in wrd if not f.isdigit()])
                        embedding_vector_fourth = embeddings_index.get(wrd)
                        if embedding_vector_fourth is not None:
                            num_words_in_embedding += 1
                            embedding_matrix[i] = embedding_vector_fourth
                            num_words_replaced += 1                              
                        else:
                            split_trial = splitter.split(wrd)                
                            if split_trial is not "":
                                for wrds in split_trial:
                                    embedding_vector_third = embeddings_index.get(wrds)
                                    if embedding_vector_third is not None:
                                        num_words_in_embedding += 1
                                        embedding_matrix[i] = embedding_vector_third
                                        num_words_replaced += 1                              
                                    else:
                                        num_words_fail_replaced += 1
                                        print("{} not in vocabulary".format(wrds))
                            else:
                                num_words_fail_replaced += 1
                                print("{} not in vocabulary".format(wrd))
      
    print("Number of words replaced: {}  Failed: {}".format(num_words_replaced, num_words_fail_replaced))           

In [33]:
tokenizer = fit_and_save_tokenizer(train_data['comment_text'])
load_embeddings(tokenizer, word_vectors)

dool's not in vocabulary
bailyite not in vocabulary
ʄ not in vocabulary
gavan not in vocabulary
dekolb not in vocabulary
027597675 not in vocabulary
alwiqi not in vocabulary
pb666 not in vocabulary
ʀ not in vocabulary
jairam not in vocabulary
supasoldier not in vocabulary
falseinformation not in vocabulary
‘west’ not in vocabulary
foundation’s not in vocabulary
riconferma not in vocabulary
draža not in vocabulary
riconferme not in vocabulary
wood' not in vocabulary
sidestrand not in vocabulary
occops not in vocabulary
infromací not in vocabulary
tijfo098 not in vocabulary
raviah not in vocabulary
tcby not in vocabulary
distributerd not in vocabulary
kangema not in vocabulary
dansiman not in vocabulary
kacian not in vocabulary
eb4f458 not in vocabulary
sekgathe not in vocabulary
thecyclothymiacollective not in vocabulary
jmorrison230582 not in vocabulary
6908271 not in vocabulary
estonisans not in vocabulary
thraco not in vocabulary
jetstreamer not in vocabulary
screamin' not in vocabul

gazimestan not in vocabulary
mozart's not in vocabulary
“solvency” not in vocabulary
senecan not in vocabulary
chemant not in vocabulary
tcks not in vocabulary
adviretisement not in vocabulary
represent' not in vocabulary
xjklfdsjkl not in vocabulary
ymb29 not in vocabulary
karmafist's not in vocabulary
henous not in vocabulary
cosnsistently not in vocabulary
21217438 not in vocabulary
idusn0813601120101108 not in vocabulary
taxation' not in vocabulary
civilizuar not in vocabulary
aaaaaaaayui not in vocabulary
yavana not in vocabulary
caussal not in vocabulary
gabberfoxx not in vocabulary
2028sbs6131s not in vocabulary
soriano's not in vocabulary
'three not in vocabulary
crowz not in vocabulary
assserts not in vocabulary
phalangiotarbi not in vocabulary
tarangam not in vocabulary
pileggi not in vocabulary
ichiu not in vocabulary
spinelma not in vocabulary
3310473 not in vocabulary
supposebut not in vocabulary
fruh not in vocabulary
corfeball not in vocabulary
writecreole not in vocabul

leprecaun not in vocabulary
nikopolis not in vocabulary
hewtt not in vocabulary
grunner not in vocabulary
blow'n' not in vocabulary
kitzmiller not in vocabulary
hogendobler not in vocabulary
boianjiu not in vocabulary
75056898 not in vocabulary
st47 not in vocabulary
sponcors not in vocabulary
sdoradus not in vocabulary
beehivekin not in vocabulary
ly0zvphfdtltaiowgeaj not in vocabulary
wwmpd not in vocabulary
face217 not in vocabulary
drumstickjuggler's not in vocabulary
guterres not in vocabulary
blacksports not in vocabulary
filibusterismoshe not in vocabulary
 ulim not in vocabulary
bain's not in vocabulary
 yap not in vocabulary
vampwillow not in vocabulary
overcategorisation not in vocabulary
salon's not in vocabulary
brasília not in vocabulary
e6tabdiamonds not in vocabulary
west' not in vocabulary
daily29 not in vocabulary
lordradish not in vocabulary
daily23 not in vocabulary
wpfc's not in vocabulary
eelection not in vocabulary
sggh not in vocabulary
tadoussac not in vocabular

kanhai not in vocabulary
goodwishes not in vocabulary
clubclaims not in vocabulary
callimachi not in vocabulary
tibtibetanbolivia not in vocabulary
flappity not in vocabulary
melanos not in vocabulary
tznkai not in vocabulary
melila not in vocabulary
fpas not in vocabulary
brisxton not in vocabulary
mrabc's not in vocabulary
puspe not in vocabulary
ballwash not in vocabulary
activist' not in vocabulary
nssdc not in vocabulary
salthe not in vocabulary
wikidashboard not in vocabulary
'legacy' not in vocabulary
mcmath not in vocabulary
cecil's not in vocabulary
bopper's not in vocabulary
cloonan not in vocabulary
churchill's not in vocabulary
m€ not in vocabulary
miquonranger03 not in vocabulary
liepitz not in vocabulary
friendpages not in vocabulary
seems—cataloged not in vocabulary
“self not in vocabulary
256247715 not in vocabulary
βασίζομαι not in vocabulary
evanier not in vocabulary
vince’s not in vocabulary
maradns not in vocabulary
93860 not in vocabulary
deripaska's not in vocabul

billinge not in vocabulary
tricotomy not in vocabulary
hasstill not in vocabulary
3'3 not in vocabulary
vennard not in vocabulary
'јун' not in vocabulary
'rishi' not in vocabulary
takesn not in vocabulary
king5 not in vocabulary
gijoecclogo not in vocabulary
articlesi not in vocabulary
promotedfpc not in vocabulary
bsinc not in vocabulary
fishbase not in vocabulary
'nam not in vocabulary
tanthony not in vocabulary
aklauncher's not in vocabulary
astrohurricane001 not in vocabulary
chidley not in vocabulary
këtij not in vocabulary
forstarters not in vocabulary
posetr not in vocabulary
strevens not in vocabulary
badgujjars not in vocabulary
sweden's not in vocabulary
soumtimes not in vocabulary
articles' not in vocabulary
ricky81682 not in vocabulary
20brandenburger not in vocabulary
jytte not in vocabulary
caesarstone's not in vocabulary
afchrw's not in vocabulary
242772 not in vocabulary
referencesto not in vocabulary
3'6 not in vocabulary
ferrelltabe7 not in vocabulary
leftennant not i

...

الجوائز not in vocabulary
verzoekjes not in vocabulary
strohmaier not in vocabulary
rodhullandemu's not in vocabulary
compy90 not in vocabulary
janeites not in vocabulary
450571622 not in vocabulary
taoisigh not in vocabulary
blackburne not in vocabulary
benewah not in vocabulary
312951 not in vocabulary
germanglophone not in vocabulary
499401 not in vocabulary
fatbum not in vocabulary
'regency not in vocabulary
npov''' not in vocabulary
20284881 not in vocabulary
marcomannia not in vocabulary
bethnahrin not in vocabulary
separtist not in vocabulary
logicus not in vocabulary
juanmann not in vocabulary
robdurbar not in vocabulary
2newsjax not in vocabulary
'plead not in vocabulary
'coopetition' not in vocabulary
buchinsky not in vocabulary
ɑe not in vocabulary
518110 not in vocabulary
horsefleet not in vocabulary
kcvu not in vocabulary
nut's not in vocabulary
heraclean not in vocabulary
reliable' not in vocabulary
ishockeyförening not in vocabulary
ukgbi not in vocabulary
nekrasov not i

reqorked not in vocabulary
queeg not in vocabulary
shaiva not in vocabulary
wallaseyan not in vocabulary
si'rumem not in vocabulary
uhmwpe not in vocabulary
pourush not in vocabulary
wrongplanet not in vocabulary
sulmues not in vocabulary
report…unless not in vocabulary
gostick not in vocabulary
brandon's not in vocabulary
'homebase not in vocabulary
germanns not in vocabulary
pop' not in vocabulary
'doubting' not in vocabulary
tsukai's not in vocabulary
tamme not in vocabulary
hobbins not in vocabulary
thasent not in vocabulary
tangut's not in vocabulary
'bard's not in vocabulary
atyourservice not in vocabulary
pondinfrontofschiavograve not in vocabulary
cluebot's not in vocabulary
tasksdays not in vocabulary
amblocked not in vocabulary
wadey4 not in vocabulary
lickins not in vocabulary
durza not in vocabulary
epparadox not in vocabulary
49738http not in vocabulary
face' not in vocabulary
'arbana' not in vocabulary
'mum' not in vocabulary
encmstr's not in vocabulary
americanisum not i

genenral not in vocabulary
wallack not in vocabulary
europasaurus not in vocabulary
pasvik not in vocabulary
duplek not in vocabulary
yamauchi not in vocabulary
writing—not not in vocabulary
najdi not in vocabulary
20predictors not in vocabulary
decamp's not in vocabulary
information — not in vocabulary
archeteypal not in vocabulary
momu not in vocabulary
copywrighted not in vocabulary
momk not in vocabulary
mooreclovesspielgman not in vocabulary
snitzler not in vocabulary
playin' not in vocabulary
2frichard not in vocabulary
shaw's not in vocabulary
mantzaris not in vocabulary
wwoooottt not in vocabulary
negoloid not in vocabulary
antineopian not in vocabulary
vgfdbghdfjjgvnbfdsjb not in vocabulary
npc’s not in vocabulary
cronin's not in vocabulary
polularity not in vocabulary
inevitble not in vocabulary
kami's not in vocabulary
promate not in vocabulary
rawats not in vocabulary
220x67 not in vocabulary
cheleken not in vocabulary
acpbg not in vocabulary
naruto's not in vocabulary
ligh

empire's not in vocabulary
npvo not in vocabulary
expectme not in vocabulary
povcheck not in vocabulary
wmtj not in vocabulary
20matrilineal not in vocabulary
dourios not in vocabulary
المطوع not in vocabulary
'wtf not in vocabulary
quickfail not in vocabulary
kiejko's not in vocabulary
480104641 not in vocabulary
sncf's not in vocabulary
don' not in vocabulary
didn’t not in vocabulary
ghostmonkey57 not in vocabulary
jvcover not in vocabulary
Øßp not in vocabulary
amptp not in vocabulary
shnitzled not in vocabulary
penis's not in vocabulary
'alleged not in vocabulary
המפלגה not in vocabulary
ihateyou not in vocabulary
'sockpuppet' not in vocabulary
tendacies not in vocabulary
adanir not in vocabulary
guyzero not in vocabulary
articleno not in vocabulary
neutralhomer's not in vocabulary
144552 not in vocabulary
'fractal' not in vocabulary
hefner’s not in vocabulary
onlineambassadors not in vocabulary
ppeeooppllee not in vocabulary
titleparts not in vocabulary
'sockpuppets not in vocabul

gritt not in vocabulary
eumetazoa not in vocabulary
nuix not in vocabulary
carlin's not in vocabulary
consisdering not in vocabulary
project’s not in vocabulary
myconos not in vocabulary
panchakam not in vocabulary
embededed not in vocabulary
delanoy not in vocabulary
“oops not in vocabulary
substantiatd not in vocabulary
timberg not in vocabulary
podsanski not in vocabulary
rabee not in vocabulary
sbs6147y7 not in vocabulary
garner's not in vocabulary
autoarchive not in vocabulary
frequentou not in vocabulary
tà£k not in vocabulary
gaurishankar not in vocabulary
stingent not in vocabulary
whatchamacall not in vocabulary
bulten not in vocabulary
amened not in vocabulary
worldwideto not in vocabulary
''everyone not in vocabulary
ziuas not in vocabulary
parkerson not in vocabulary
1917–1957 not in vocabulary
Βελιεωε not in vocabulary
Ŧ'''''' not in vocabulary
3°c not in vocabulary
bastianini not in vocabulary
desudesudesudesudesudesudesudesudesudesudesudesudesudesu not in vocabulary
첫 no

In [63]:
tokenizer = fit_and_save_tokenizer(train_data['comment_text'])
load_embeddings(tokenizer, word_vectors)

dools not in vocabulary
bailyite not in vocabulary
 not in vocabulary
gavan not in vocabulary
dekolb not in vocabulary
027597675 not in vocabulary
alwiqi not in vocabulary
pb666 not in vocabulary
 not in vocabulary
jairam not in vocabulary
supasoldier not in vocabulary
falseinformation not in vocabulary
riconferma not in vocabulary
riconferme not in vocabulary
sidestrand not in vocabulary
occops not in vocabulary
infromac not in vocabulary
tijfo098 not in vocabulary
raviah not in vocabulary
tcby not in vocabulary
distributerd not in vocabulary
kangema not in vocabulary
dansiman not in vocabulary
kacian not in vocabulary
eb4f458 not in vocabulary
sekgathe not in vocabulary
thecyclothymiacollective not in vocabulary
jmorrison230582 not in vocabulary
6908271 not in vocabulary
estonisans not in vocabulary
thraco not in vocabulary
jetstreamer not in vocabulary
gayyyyyyyyyyy not in vocabulary
 not in vocabulary
jadams7831 not in vocabulary
beejaypii not in vocabulary
conrtibs not in vocabula

myhr not in vocabulary
ryvarta not in vocabulary
sortnumber not in vocabulary
 not in vocabulary
2099996 not in vocabulary
illustarte not in vocabulary
banyantree not in vocabulary
mzilikazi not in vocabulary
mirataeus not in vocabulary
mercurynews not in vocabulary
mgay not in vocabulary
 not in vocabulary
ccinsider not in vocabulary
966197 not in vocabulary
canadaeast not in vocabulary
oceanbeach not in vocabulary
extravascanza not in vocabulary
bluffview not in vocabulary
suwol not in vocabulary
vmpu6wxkigd8qhmgigydw not in vocabulary
danski not in vocabulary
reftools not in vocabulary
anticommiemike not in vocabulary
philippes not in vocabulary
civiilzed not in vocabulary
poved not in vocabulary
vmaxbike not in vocabulary
davisjune not in vocabulary
macrakides not in vocabulary
hoineff not in vocabulary
encyclotadd not in vocabulary
rasterb not in vocabulary
dositejs not in vocabulary
20dies not in vocabulary
5b43872721 not in vocabulary
airys not in vocabulary
bubba73 not in vocab

bahaullah not in vocabulary
mctrain not in vocabulary
leonahelen not in vocabulary
commp3 not in vocabulary
canonicalise not in vocabulary
wikicookie not in vocabulary
inogolo not in vocabulary
glazovs not in vocabulary
hardings not in vocabulary
thearcadiannewspaper not in vocabulary
potverduju not in vocabulary
dissostichus not in vocabulary
amillenialists not in vocabulary
mosson not in vocabulary
ctjf83s not in vocabulary
chepeer not in vocabulary
trudelllomenzo not in vocabulary
nataliu not in vocabulary
70cttbmkdcbqraebzmwccg not in vocabulary
gwydir not in vocabulary
hyrcanian not in vocabulary
img440 not in vocabulary
seanyakaralphy not in vocabulary
san1 not in vocabulary
nory not in vocabulary
techinc not in vocabulary
tankman not in vocabulary
articleexists not in vocabulary
defeaturing not in vocabulary
words63 not in vocabulary
exonim not in vocabulary
nihiltres not in vocabulary
lagerphone not in vocabulary
minglink not in vocabulary
spaker not in vocabulary
danahs not in

ericg not in vocabulary
dlickheads not in vocabulary
websources not in vocabulary
baums not in vocabulary
hellobc not in vocabulary
living2 not in vocabulary
aekbasket not in vocabulary
callinicos not in vocabulary
yiar not in vocabulary
 not in vocabulary
outerlimits not in vocabulary
yanklowitz not in vocabulary
hnpcc not in vocabulary
wispanow not in vocabulary
sweeton not in vocabulary
nittyg not in vocabulary
atabselect not in vocabulary
mountaints not in vocabulary
 not in vocabulary
tsondue not in vocabulary
jaisimha not in vocabulary
trifunovic not in vocabulary
aquabuddha not in vocabulary
antisemit not in vocabulary
funketeer not in vocabulary
 not in vocabulary
eurovelo not in vocabulary
crismus not in vocabulary
dcs47 not in vocabulary
svres not in vocabulary
marcinko not in vocabulary
vanadlism not in vocabulary
mabbett not in vocabulary
noyon not in vocabulary
death68 not in vocabulary
vrabbeinu not in vocabulary
silverxblaze not in vocabulary
otrher not in vocabulary
lei

prairiewood not in vocabulary
russifying not in vocabulary
kahanism not in vocabulary
tagteaming not in vocabulary
tsismisan not in vocabulary
fornvnner not in vocabulary
cma662a not in vocabulary
bibek not in vocabulary
mariconite not in vocabulary
talkim not in vocabulary
caravaggisti not in vocabulary
wulfnoth not in vocabulary
wachanaruka not in vocabulary
failakah not in vocabulary
videhas not in vocabulary
ozurbanmusics not in vocabulary
geova not in vocabulary
dixiercat not in vocabulary
firstmark not in vocabulary
32858872 not in vocabulary
pronoucation not in vocabulary
pandp not in vocabulary
nrsimha not in vocabulary
trannybangers not in vocabulary
schilstra not in vocabulary
6tabnatural not in vocabulary
oughton not in vocabulary
lbhscs not in vocabulary
pushtuns not in vocabulary
studiying not in vocabulary
naranjotab not in vocabulary
userspacedrafts not in vocabulary
namenicknamemma not in vocabulary
wiesenthal not in vocabulary
gfdl1 not in vocabulary
tahirih not in voc

...

15478316 not in vocabulary
tablonger not in vocabulary
gorgonzilla not in vocabulary
tabwar not in vocabulary
bvcause not in vocabulary
26d3mgwv not in vocabulary
cauchys not in vocabulary
321b not in vocabulary
jusitify not in vocabulary
eqation not in vocabulary
morethan3word not in vocabulary
28800969120 not in vocabulary
cptnonon not in vocabulary
considerble not in vocabulary
berulis not in vocabulary
2016sankars not in vocabulary
welcomescreen not in vocabulary
avantar not in vocabulary
malcome not in vocabulary
larverna not in vocabulary
outproxy not in vocabulary
soboteurs not in vocabulary
nilakanta not in vocabulary
t8asv1zc9lbmjkgpzvg4yq2ljme not in vocabulary
seawright not in vocabulary
rojava not in vocabulary
1199704 not in vocabulary
20080804220345aazewck not in vocabulary
bellotti not in vocabulary
blitle not in vocabulary
639tab not in vocabulary
philipo not in vocabulary
bourries not in vocabulary
pagehelp not in vocabulary
yenti not in vocabulary
vandlaism not in voc

everytopicintheuniverseexceptchickens not in vocabulary
dicoese not in vocabulary
wpnotrs not in vocabulary
equelly not in vocabulary
eleftherios not in vocabulary
2008050903 not in vocabulary
 not in vocabulary
ccker not in vocabulary
gotama not in vocabulary
administerial not in vocabulary
spgqnil8ur1 not in vocabulary
eurasiatic not in vocabulary
convics not in vocabulary
lnocw not in vocabulary
nyyyy not in vocabulary
jashobanti not in vocabulary
defamotories not in vocabulary
gillings not in vocabulary
kimberlin not in vocabulary
badgehunter not in vocabulary
excitnace not in vocabulary
kalsang not in vocabulary
traiditional not in vocabulary
numidian not in vocabulary
languageor not in vocabulary
exactsame not in vocabulary
respondend not in vocabulary
hahaheeahhggghhhh not in vocabulary
stowarzyszenia not in vocabulary
865327 not in vocabulary
kven not in vocabulary
dandan09 not in vocabulary
discontents3nov07 not in vocabulary
termsbut not in vocabulary
rancorbut not in vocabul

theshiznit not in vocabulary
wpvi not in vocabulary
wpvg not in vocabulary
nakhichevans not in vocabulary
slandarous not in vocabulary
ebla not in vocabulary
caage not in vocabulary
xcoraw not in vocabulary
dohoho not in vocabulary
zeibura not in vocabulary
kailis not in vocabulary
eveteyhthing not in vocabulary
zntrip not in vocabulary
oreillys not in vocabulary
doye not in vocabulary
jugoslavian not in vocabulary
thribb2 not in vocabulary
evenhuis not in vocabulary
routeledge not in vocabulary
ralian not in vocabulary
 not in vocabulary
zulfikar not in vocabulary
impreion not in vocabulary
siever not in vocabulary
clayc not in vocabulary
fitinizini not in vocabulary
jomicoe not in vocabulary
chocky60 not in vocabulary
solicitate not in vocabulary
sarkeensian not in vocabulary
federalreserve not in vocabulary
iz3w not in vocabulary
wikimod not in vocabulary
 not in vocabulary
johndarth not in vocabulary
doorgunner01a not in vocabulary
quackguru not in vocabulary
marenzio not in vocabu

supoprts not in vocabulary
ozaru not in vocabulary
agamudayar not in vocabulary
murgotroyd not in vocabulary
golzs not in vocabulary
realies not in vocabulary
eldumpo not in vocabulary
archieological not in vocabulary
infitive not in vocabulary
catagorization not in vocabulary
solocommand not in vocabulary
rjecina2 not in vocabulary
lobaus not in vocabulary
butlerian not in vocabulary
talkcont not in vocabulary
ondrej not in vocabulary
jeanettepink not in vocabulary
003417 not in vocabulary
nasliduju not in vocabulary
omahony not in vocabulary
mordros not in vocabulary
sandifers not in vocabulary
populationdecrease not in vocabulary
mmisinformation not in vocabulary
vendetta97 not in vocabulary
girondists not in vocabulary
48281 not in vocabulary
scebeli not in vocabulary
598129317 not in vocabulary
propol not in vocabulary
kommandohimmler not in vocabulary
chricton not in vocabulary
katr67 not in vocabulary
mahalingam not in vocabulary
antonietta not in vocabulary
theroadislong not in

benedictines not in vocabulary
carfou not in vocabulary
cma311b not in vocabulary
regurgigating not in vocabulary
suxxor not in vocabulary
yname not in vocabulary
amuchastegui not in vocabulary
presumingly not in vocabulary
glossologist not in vocabulary
asterid not in vocabulary
poleszuk not in vocabulary
extroneous not in vocabulary
manatm not in vocabulary
heuschrecke not in vocabulary
fermanlar not in vocabulary
glad78 not in vocabulary
rbaishs not in vocabulary
wikiubx not in vocabulary
exculpuatory not in vocabulary
postis not in vocabulary
145899968 not in vocabulary
mashaunix not in vocabulary
hehehehehehehehehehheheheehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehehhehehehehehehehehe not in vocabulary
201819 not in vocabulary
slready not in vocabulary
b361 not in vocabulary
petitte not in vocabulary
xrap not in vocabulary
eb6 not in vocabulary
aksungur not in vocabulary
k

In [55]:
tokenizer = fit_and_save_tokenizer(train_data['comment_text'])
load_embeddings(tokenizer, word_vectors)

 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
nicknamer not in vocabulary
 not in vocabulary
 not in vocabulary
songfulness not in vocabulary
Elonore not in vocabulary
homager not in vocabulary
forebodingness not in vocabulary
 not in vocabulary
Fredek not in vocabulary
 not in vocabulary
Evaleen not in vocabulary
 not in vocabulary
 not in vocabulary
troths not in vocabulary
 not in vocabulary
 not in vocabulary
Agnesse not in vocabulary
 not in vocabulary
 not in vocabulary
inchoates not in vocabulary
[] not in vocabulary List is empty
Sherlocke not in vocabulary
 not in vocabulary
attributer not in vocabulary
 not in vocabulary
unharnesses not in vocabulary
 not in vocabulary
 not in vocabulary
Saraann not in vocabulary
philanders not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
matricides not in vocabulary
crossbarred not in vocabula

 not in vocabulary
 not in vocabulary
 not in vocabulary
moderatenesses not in vocabulary
Ingamar not in vocabulary
jiujitsus not in vocabulary
subcomputation not in vocabulary
 not in vocabulary
archfiends not in vocabulary
 not in vocabulary
foxtrotting not in vocabulary
electroencephalographs not in vocabulary
adverseness not in vocabulary
 not in vocabulary
 not in vocabulary
Maurise not in vocabulary
 not in vocabulary
swampiest not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
undergrounder not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Husains not in vocabulary
jurisprudences not in vocabulary
 not in vocabulary
prospectiveness not in vocabulary
whitings not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
ergophobia not in vocabulary
Joseito not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabular

maydays not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
trinketed not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
outargued not in vocabulary
Reichstags not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
bluffness not in vocabulary
whippletrees not in vocabulary
baconer not in vocabulary
 not in vocabulary
 not in vocabulary
babels not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
angelicas not in vocabulary
cartages not in vocabulary
Annadiana not in vocabulary
familiarizer not in vocabulary
 not in vocabulary
Walliw not in vocabulary
[] not in vocabulary List is empty
 not in vocabulary
desirabilia not in vocabulary
 not in vocabulary
 not in vocabulary
timothies not in vocabulary
 not in vocabulary
differer not in vocabulary
Ingeberg not 

 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
Aguistin not in vocabulary
 not in vocabulary
Gayel not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
maladapt not in vocabulary
diapasons not in vocabulary
 not in vocabulary
readabilities not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
seasonableness not in vocabulary
Liuka not in vocabulary
 not in vocabulary
channelizes not in vocabulary
Bentlee not in vocabulary
Dalenna not in vocabulary
haggards not in vocabulary
 not in vocabulary
 not in vocabulary
gallanting not in vocabulary
 not in vocabulary
palladiums not in vocabulary
 not in vocabulary
intracohort not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Ursola not in vocabulary
Devondra not in vocabulary
 not in voc

clamorer not in vocabulary
 not in vocabulary
 not in vocabulary
Rayshell not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
promenader not in vocabulary
balefuller not in vocabulary
nonbelligerent not in vocabulary
 not in vocabulary
barning not in vocabulary
Aubine not in vocabulary
crowbait not in vocabulary
 not in vocabulary
Heinrik not in vocabulary
 not in vocabulary
nerviness not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
augustness not in vocabulary
burnables not in vocabulary
 not in vocabulary
halfheartedness not in vocabulary
 not in vocabulary
Allianora not in vocabulary
 not in vocabulary
empaneling not in vocabulary
 not in vocabulary
 not in vocabulary
garred not in vocabulary
 not in vocabulary
 not in vocabulary
mananas not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
Indianian not in 

...

 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
buddings not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
knowledgeableness not in vocabulary
figurativeness not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
nontheatrical not in vocabulary
patriotisms not in vocabulary
unpartizan not in vocabulary
mannas not in vocabulary
farfetchedness not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
misrepresenter not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Godthaab not in vocabulary
affrication not in vocabulary
 not in vocabulary
Wylma not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
 not in vocabulary
 not in vocabulary
aliyahs not in vocabulary
Daffi not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Alberik not in vocabulary
 

[] not in vocabulary List is empty
lovelinesses not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
diagrammaticality not in vocabulary
courteousnesses not in vocabulary
militarisms not in vocabulary
Reichstags not in vocabulary
bonhomies not in vocabulary
 not in vocabulary
Rafaelia not in vocabulary
 not in vocabulary
 not in vocabulary
Staffard not in vocabulary
Gerhardine not in vocabulary
dudder not in vocabulary
aliyahs not in vocabulary
polytheisms not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
 not in vocabulary
Hobard not in vocabulary
subcomputation not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Barbabas not in vocabulary
 not in vocabulary
 not in vocabulary
houseworkers not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
unneutralized not in vocabulary
 not in vocabulary
 not in voca

 not in vocabulary
 not in vocabulary
camaraderies not in vocabulary
 not in vocabulary
Beitris not in vocabulary
vigilantist not in vocabulary
 not in vocabulary
Chiarra not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
greenswards not in vocabulary
 not in vocabulary
burnables not in vocabulary
flecker not in vocabulary
speedboating not in vocabulary
netts not in vocabulary
 not in vocabulary
 not in vocabulary
Nefen not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
wainwrights not in vocabulary
 not in vocabulary
electromyographically not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
[] not in vocabulary List is empty
 not in vocabulary
ciceroni not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Bar

consumerisms not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
tandooris not in vocabulary
krills not in vocabulary
 not in vocabulary
polychemicals not in vocabulary
 not in vocabulary
foxtrotting not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Gwenore not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
poloniums not in vocabulary
estimableness not in vocabulary
burier not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
Christianizes not in vocabulary
paregorics not in vocabulary
 not in vocabulary
centralizations not in vocabulary
metacarpi not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in voca

brontosaurs not in vocabulary
[] not in vocabulary List is empty
ethnologies not in vocabulary
 not in vocabulary
misguidedness not in vocabulary
[] not in vocabulary List is empty
 not in vocabulary
kriegspiel not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
stinkingly not in vocabulary
 not in vocabulary
beriberis not in vocabulary
sinisterness not in vocabulary
connotatively not in vocabulary
fortunateness not in vocabulary
 not in vocabulary
 not in vocabulary
rookier not in vocabulary
Finnbogadottir not in vocabulary
Bidget not in vocabulary
 not in vocabulary
emeritae not in vocabulary
 not in vocabulary
 not in vocabulary
triphosphopyridine not in vocabulary
metricize not in vocabulary
 not in vocabulary
Shanghaiing not in vocabulary
 not in vocabulary
 not in vocabulary
velarize not in vocabulary
skyscrape not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
 not in vocabulary
superfix not in vocabulary
Enrichet

In [59]:
trial = pd.read_csv('git/Kaggle/train.csv')
display(cmt.head(n=20))


0     Explanation\nWhy the edits made under my usern...
1     D'aww! He matches this background colour I'm s...
2     Hey man, I'm really not trying to edit war. It...
3     "\nMore\nI can't make any real suggestions on ...
4     You, sir, are my hero. Any chance you remember...
5     "\n\nCongratulations from me as well, use the ...
6          COCKSUCKER BEFORE YOU PISS AROUND ON MY WORK
7     Your vandalism to the Matt Shirvington article...
8     Sorry if the word 'nonsense' was offensive to ...
9     alignment on this subject and which are contra...
10    "\nFair use rationale for Image:Wonju.jpg\n\nT...
11    bbq \n\nbe a man and lets discuss it-maybe ove...
12    Hey... what is it..\n@ | talk .\nWhat is it......
13    Before you start throwing accusations and warn...
14    Oh, and the girl above started her arguments w...
15    "\n\nJuelz Santanas Age\n\nIn 2002, Juelz Sant...
16    Bye! \n\nDon't look, come or think of comming ...
17     REDIRECT Talk:Voydan Pop Georgiev- Cherno

In [71]:
checker =  enchant.Dict("en_US")
#cmt.map(lambda x: checker.suggest(x)[0])
def process_str(row_str):
   # return (row_str.strip("'"))
    return row_str.replace(' ', '')

trial['comment_text'].apply(process_str)
display(trial.head(n=20))


id                                       comment_text  \
0   0000997932d777bf  Explanation\nWhy the edits made under my usern...   
1   000103f0d9cfb60f  D'aww! He matches this background colour I'm s...   
2   000113f07ec002fd  Hey man, I'm really not trying to edit war. It...   
3   0001b41b1c6bb37e  "\nMore\nI can't make any real suggestions on ...   
4   0001d958c54c6e35  You, sir, are my hero. Any chance you remember...   
5   00025465d4725e87  "\n\nCongratulations from me as well, use the ...   
6   0002bcb3da6cb337       COCKSUCKER BEFORE YOU PISS AROUND ON MY WORK   
7   00031b1e95af7921  Your vandalism to the Matt Shirvington article...   
8   00037261f536c51d  Sorry if the word 'nonsense' was offensive to ...   
9   00040093b2687caa  alignment on this subject and which are contra...   
10  0005300084f90edc  "\nFair use rationale for Image:Wonju.jpg\n\nT...   
11  00054a5e18b50dd4  bbq \n\nbe a man and lets discuss it-maybe ove...   
12  0005c987bdfc9d4b  Hey... what is it..\n@ | talk .\nWhat is it......   
13  0006f16e4e9f292e  Before you start throwing accusations and warn...   
14  00070ef96486d6f9  Oh, and the girl above started her arguments w...   
15  00078f8ce7eb276d  "\n\nJuelz Santanas Age\n\nIn 2002, Juelz Sant...   
16  0007e25b2121310b  Bye! \n\nDon't look, come or think of comming ...   
17  000897889268bc93   REDIRECT Talk:Voydan Pop Georgiev- Chernodrinski   
18  0009801bd85e5806  The Mitsurugi point made no sense - why not ar...   
19  0009eaea3325de8c  Don't mean to bother you \n\nI see that you're...   

    toxic  severe_toxic  obscene  threat  insult  identity_hate  
0       0             0        0       0       0              0  
1       0             0        0       0       0              0  
2       0             0        0       0       0              0  
3       0             0        0       0       0              0  
4       0             0        0       0       0              0  
5       0             0        0       0       0              0  
6       1             1        1       0       1              0  
7       0             0        0       0       0              0  
8       0             0        0       0       0              0  
9       0             0        0       0       0              0  
10      0             0        0       0       0              0  
11      0             0        0       0       0              0  
12      1             0        0       0       0              0  
13      0             0        0       0       0              0  
14      0             0        0       0       0              0  
15      0             0        0       0       0              0  
16      1             0        0       0       0              0  
17      0             0        0       0       0              0  
18      0             0        0       0       0              0  
19      0             0        0       0       0              0

In [10]:
trial = pd.read_csv('stage_one_ensemble_features/combined_meta.csv').drop('id', axis = 1)

train_label = pd.read_csv('final_train.csv')

test = pd.read_csv('stage_one_ensemble_features/test/meta_ensemble_test.csv').drop('id', axis = 1)


In [15]:
display(trial.head(n=20))

capitals  num_unique_words  num_exclamation_marks  num_punctuation  \
0   2.890372          3.737670                      0         1.945910   
1   2.197225          2.890372                      1         1.791759   
2   1.609438          3.688879                      0         1.609438   
3   2.484907          4.418841                      0         1.945910   
4   1.098612          2.639057                      0         1.386294   
5   0.693147          2.564949                      0         1.098612   
6   3.637586          2.197225                      0         0.000000   
7   1.609438          3.044522                      0         1.386294   
8   2.079442          4.262680                      0         2.302585   
9   1.098612          2.564949                      0         0.000000   
10  3.988984          5.402677                      0         4.043051   
11  0.000000          2.484907                      0         0.000000   
12  3.784190          3.931826                      0         2.833213   
13  1.945910          4.691348                      0         2.708050   
14  2.197225          3.465736                      0         2.079442   
15  3.367296          4.543295                      0         2.772589   
16  1.386294          2.397895                      2         1.098612   
17  2.639057          1.791759                      0         0.693147   
18  1.791759          2.995732                      0         0.000000   
19  1.791759          4.143135                      0         1.386294   

     toxic-a  severe_toxic-a  obscene-a  threat-a  insult-a  identity_hate-a  \
0   0.020052        0.000172   0.004895  0.000009  0.004707         0.000191   
1   0.120857        0.003638   0.057968  0.000012  0.037449         0.002114   
2   0.013945        0.000713   0.002814  0.000004  0.003211         0.000094   
3   0.000969        0.000030   0.000708  0.000010  0.000387         0.000144   
4   0.065857        0.000799   0.037083  0.000079  0.029953         0.000551   
5   0.008962        0.000155   0.005418  0.000125  0.006372         0.000222   
6   0.948445        0.546873   0.964787  0.002511  0.870642         0.012368   
7   0.077494        0.000849   0.035757  0.004910  0.022695         0.000424   
8   0.009515        0.000058   0.002625  0.000006  0.002876         0.000269   
9   0.044735        0.001380   0.014605  0.000127  0.023963         0.001932   
10  0.003349        0.000048   0.001828  0.000005  0.000275         0.000169   
11  0.053676        0.002421   0.018360  0.001199  0.009410         0.002395   
12  0.048584        0.000060   0.012649  0.000019  0.002401         0.000302   
13  0.092242        0.000094   0.005338  0.000096  0.024431         0.000387   
14  0.074170        0.001610   0.052821  0.000040  0.017798         0.002918   
15  0.023108        0.003158   0.008163  0.000053  0.006666         0.001737   
16  0.124986        0.003207   0.035925  0.000557  0.032427         0.002697   
17  0.022920        0.000626   0.005541  0.000098  0.005105         0.000916   
18  0.030039        0.001578   0.003491  0.000011  0.014697         0.000810   
19  0.026125        0.000289   0.006253  0.000100  0.010717         0.000347   

         ...            obscene-b      threat-b  insult-b  identity_hate-b  \
0        ...         4.386071e-04  1.589602e-06  0.000171         0.000027   
1        ...         4.014467e-04  3.413729e-05  0.000035         0.000243   
2        ...         2.197055e-03  1.161840e-04  0.000982         0.000057   
3        ...         1.717578e-04  4.425572e-05  0.000013         0.000113   
4        ...         4.972179e-03  1.665751e-04  0.011593         0.001136   
5        ...         2.247388e-07  3.394539e-07  0.000006         0.000009   
6        ...         8.258977e-01  2.701001e-04  0.296263         0.002003   
7        ...         3.699794e-04  5.190443e-04  0.001582         0.000912   
8        ...         5.198229e-05  1.697967e-06  0.000014         

In [75]:
lens.hist()

In [76]:
label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']
trial['none'] = 1-trial[label_cols].max(axis=1)
trial.describe()

toxic   severe_toxic        obscene         threat  \
count  159571.000000  159571.000000  159571.000000  159571.000000   
mean        0.095844       0.009996       0.052948       0.002996   
std         0.294379       0.099477       0.223931       0.054650   
min         0.000000       0.000000       0.000000       0.000000   
25%         0.000000       0.000000       0.000000       0.000000   
50%         0.000000       0.000000       0.000000       0.000000   
75%         0.000000       0.000000       0.000000       0.000000   
max         1.000000       1.000000       1.000000       1.000000   

              insult  identity_hate           none  
count  159571.000000  159571.000000  159571.000000  
mean        0.049364       0.008805       0.898321  
std         0.216627       0.093420       0.302226  
min         0.000000       0.000000       0.000000  
25%         0.000000       0.000000       1.000000  
50%         0.000000       0.000000       1.000000  
75%         0.000000       0.000000       1.000000  
max         1.000000       1.000000       1.000000

In [12]:
len(train_label),len(test)

(638284, 153164)

In [11]:
COMMENT = 'comment_text'
trial.fillna("0", inplace=True)
test.fillna("0", inplace=True)

In [85]:
import re, string
import pandas as pd, numpy as np
from sklearn.linear_model import LogisticRegression
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

re_tok = re.compile('([{string.punctuation}“”¨«»®´·º½¾¿¡§£₤‘’])')

def tokenize(s):
    return re_tok.sub(r' \1 ', s).split()

In [86]:
n = trial.shape[0]
vec = TfidfVectorizer(ngram_range=(1,2), tokenizer=tokenize,
               min_df=3, max_df=0.9, strip_accents='unicode', use_idf=1,
               smooth_idf=1, sublinear_tf=1 )
trn_term_doc = vec.fit_transform(trial[COMMENT])
test_term_doc = vec.transform(test[COMMENT])

In [87]:
trn_term_doc, test_term_doc

(<159571x74624 sparse matrix of type '<type 'numpy.float64'>'
 	with 26085258 stored elements in Compressed Sparse Row format>,
 <153164x74624 sparse matrix of type '<type 'numpy.float64'>'
 	with 22593990 stored elements in Compressed Sparse Row format>)

In [88]:
def pr(y_i, y):
    p = x[y==y_i].sum(0)
    return (p+1) / ((y==y_i).sum()+1)

In [6]:
x = trial
test_x = test

In [3]:
####META LR
def get_mdl(train_x,y):
    param_grid = {'C': [0.001, 0.01, 0.1, 1, 10, 100, 1000]}
    y = y.values
    #m = LogisticRegression(C=4, dual=True)
    clf = GridSearchCV(LogisticRegression(dual=True), param_grid, scoring = 'roc_auc')    
    x_nb = train_x
    return clf.fit(x_nb, y)

In [9]:
def get_mdl(y):
    y = y.values
    m = LogisticRegression(C=4, dual=True)
    x_nb = x.multiply(r)
    return m.fit(x_nb, y)

In [91]:
label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']

preds = np.zeros((len(test), len(label_cols)))

for i, j in enumerate(label_cols):
    print('fit', j)
    m,r = get_mdl(train_label[j])
    preds[:,i] = m.predict_proba(test_x.multiply(r))[:,1]

('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')


In [12]:
def train_model(train_x, train_y, val_x, val_y, text_x):
    final_label = ['capitals','num_unique_words', 'num_exclamation_marks', 'num_punctuation', 'toxic-a', 'severe_toxic-a', 'obscene-a', 'threat-a', 'insult-a', 'identity_hate-a','toxic-b', 'severe_toxic-b', 'obscene-b', 'threat-b', 'insult-b', 'identity_hate-b','toxic-c', 'severe_toxic-c', 'obscene-c', 'threat-c', 'insult-c', 'identity_hate-c']
    indexing_folds = ['a','b','c']
    test = pd.read_csv('test.csv')
    label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']
    preds = np.zeros((len(test), len(label_cols)))
    meta = np.zeros((val_x.shape[0], len(label_cols)))
    for i, j in enumerate(label_cols):
        xtra = ['capitals','num_unique_words', 'num_exclamation_marks', 'num_punctuation']
        for index in indexing_folds:
            three_pred = j + '-' + index
            xtra.append(three_pred)
        train_x = pd.DataFrame(train_x, columns = final_label)
        val_x = pd.DataFrame(val_x, columns = final_label)
        train_x_sample = train_x[xtra]
        val_x_sample = val_x[xtra]
        test_x_sample = test_x[xtra]
        print('fit', j)
        label_train = pd.DataFrame(train_y, columns = label_cols)
        m = get_mdl(train_x_sample, label_train[j])
        meta[:,i] = m.best_estimator_.predict_proba(val_x_sample)[:,1]
        preds[:,i] = m.best_estimator_.predict_proba(test_x_sample)[:,1]
    return preds, meta

In [13]:
X = trial
y = train_label[['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']]
fold_size = len(X) // 10
test_predicts_list = []

total_meta = []
for fold_id in range(0, 10):
    fold_start = fold_size * fold_id
    fold_end = fold_start + fold_size
            
    if fold_id == fold_size - 1:
        fold_end = len(X)
    
    train_x = np.concatenate([X[:fold_start], X[fold_end:]])
    train_y = np.concatenate([y[:fold_start], y[fold_end:]])
    #print(train_y.shape)
    val_x = X[fold_start:fold_end]
    val_y = y[fold_start:fold_end]
       
    #train_x = vec.transform(train_x)
    #val_x = vec.transform(val_x)
        
    test_predicts, meta = train_model(train_x, train_y, val_x, val_y, test_x)
    test_predicts_list.append(test_predicts)
    if (fold_id == 0):
        total_meta = meta
    else:
        total_meta = np.concatenate((total_meta, meta), axis=0)
    print("finish fold {}".format(fold_id))

('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 0
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 1
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 2
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 3
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 4
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 5
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obscene')
('fit', 'threat')
('fit', 'insult')
('fit', 'identity_hate')
finish fold 6
('fit', 'toxic')
('fit', 'severe_toxic')
('fit', 'obsce

In [16]:
subm = pd.read_csv('sample_submission.csv')
submid = pd.DataFrame({'id': subm["id"]})
total_meta_data = pd.concat([submid, pd.DataFrame(total_meta, columns = label_cols)], axis=1)
total_meta_data.to_csv('stage2_meta_feature_nbsvm_xgb_gru_withLR_filtered.csv', index=False)

In [17]:
test_predicts = np.ones(test_predicts_list[0].shape)
for fold_predict in test_predicts_list:
    test_predicts *= fold_predict

test_predicts **= (1. / len(test_predicts_list))

In [18]:
test_predicts.shape

(153164, 6)

In [19]:
subm = pd.read_csv('sample_submission.csv')
submid = pd.DataFrame({'id': subm["id"]})
label_cols = ['toxic', 'severe_toxic', 'obscene', 'threat', 'insult', 'identity_hate']
submission = pd.concat([submid, pd.DataFrame(test_predicts, columns = label_cols)], axis=1)


In [21]:
display(submission.head(n=20))

id     toxic  severe_toxic   obscene    threat    insult  \
0   00001cee341fdb12  0.998525      0.393846  0.999002  0.000381  0.997577   
1   0000247867823ef7  0.008010      0.002483  0.003836  0.000518  0.004056   
2   00013b17ad220c46  0.006002      0.002578  0.004217  0.000742  0.004362   
3   00017563c3f7919a  0.003525      0.001298  0.003261  0.000358  0.003564   
4   00017695ad8997eb  0.005896      0.002014  0.003784  0.000500  0.004095   
5   0001ea8717f6de06  0.003992      0.001617  0.003493  0.000443  0.003900   
6   00024115d4cbde0f  0.003641      0.001409  0.003256  0.000368  0.003630   
7   000247e83dcc1211  0.036596      0.002035  0.004094  0.000432  0.004051   
8   00025358d4737918  0.005294      0.001492  0.003103  0.000342  0.003454   
9   00026d1092fe71cc  0.003787      0.001407  0.003215  0.000360  0.003541   
10  0002eadc3b301559  0.156098      0.001465  0.034748  0.000457  0.004329   
11  0002f87b16116a7f  0.004546      0.001279  0.003157  0.000331  0.003510   
12  0003806b11932181  0.003550      0.001247  0.003093  0.000317  0.003421   
13  0003e1cccfd5a40a  0.005499      0.001722  0.003239  0.000391  0.003574   
14  00059ace3e3e9a53  0.003181      0.001141  0.003099  0.000334  0.003463   
15  000634272d0d44eb  0.006175      0.002057  0.004029  0.000572  0.005098   
16  000663aff0fffc80  0.004022      0.002045  0.003913  0.000595  0.004238   
17  000689dd34e20979  0.006897      0.001355  0.004220  0.000374  0.003670   
18  000834769115370c  0.003377      0.001146  0.003018  0.000304  0.003369   
19  000844b52dee5f3f  0.004258      0.002286  0.003836  0.000506  0.004010   

    identity_hate  
0        0.019173  
1        0.001132  
2        0.001296  
3        0.000880  
4        0.001124  
5        0.001015  
6        0.000895  
7        0.001081  
8        0.000803  
9        0.000875  
10       0.001001  
11       0.000812  
12       0.000813  
13       0.000867  
14       0.000836  
15       0.001122  
16       0.001248  
17       0.000909  
18       0.000787  
19       0.001159

In [94]:
subm = pd.read_csv('~/git/Kaggle/sample_submission.csv')
submid = pd.DataFrame({'id': subm["id"]})
submission = pd.concat([submid, pd.DataFrame(preds, columns = label_cols)], axis=1)
display(submission.head(n=20))

id     toxic  severe_toxic   obscene    threat    insult  \
0   00001cee341fdb12  0.980160      0.225000  0.981705  0.004439  0.850927   
1   0000247867823ef7  0.035314      0.018774  0.011345  0.000994  0.021025   
2   00013b17ad220c46  0.024430      0.001458  0.014841  0.000131  0.002879   
3   00017563c3f7919a  0.008019      0.000297  0.004546  0.000199  0.007296   
4   00017695ad8997eb  0.071051      0.000996  0.007717  0.000079  0.016191   
5   0001ea8717f6de06  0.016865      0.000230  0.002620  0.000185  0.019998   
6   00024115d4cbde0f  0.009054      0.000445  0.004746  0.000092  0.006479   
7   000247e83dcc1211  0.052937      0.001113  0.018366  0.000508  0.009682   
8   00025358d4737918  0.010785      0.000215  0.003566  0.000079  0.008627   
9   00026d1092fe71cc  0.004456      0.000217  0.001037  0.000098  0.001696   
10  0002eadc3b301559  0.114065      0.006946  0.070234  0.001858  0.041872   
11  0002f87b16116a7f  0.082894      0.000948  0.022681  0.000316  0.026183   
12  0003806b11932181  0.006445      0.000334  0.001735  0.000069  0.001699   
13  0003e1cccfd5a40a  0.006776      0.000339  0.004382  0.000086  0.002842   
14  00059ace3e3e9a53  0.002763      0.000374  0.003702  0.000043  0.001181   
15  000634272d0d44eb  0.098950      0.003481  0.022501  0.000094  0.036470   
16  000663aff0fffc80  0.020422      0.001470  0.004842  0.000209  0.008232   
17  000689dd34e20979  0.058663      0.001090  0.022366  0.000082  0.011553   
18  000834769115370c  0.000881      0.000075  0.000264  0.000031  0.000319   
19  000844b52dee5f3f  0.011480      0.002451  0.001353  0.000252  0.003951   

    identity_hate  
0        0.052034  
1        0.000852  
2        0.000326  
3        0.000924  
4        0.000256  
5        0.000883  
6        0.000715  
7        0.000933  
8        0.000386  
9        0.000351  
10       0.007402  
11       0.001013  
12       0.000403  
13       0.001417  
14       0.000130  
15       0.000536  
16       0.000965  
17       0.000662  
18       0.000081  
19       0.000943

In [20]:
submission.to_csv('stage1_stacking_nbsvm_xgb_gru_withLR_filtered.csv', index=False)

In [ ]:
subm = pd.read_csv('~/git/Kaggle/sample_submission.csv')
submid = pd.DataFrame({'id': subm["id"]})
total_meta_data = pd.concat([submid, pd.DataFrame(total_meta, columns = label_cols)], axis=1)
